# Feuille de travaux pratiques. Méthodes directes de résolution des systèmes linéaires (deuxième partie)

In [ ]:
# chargement des bibliothèques
import numpy as np

## Exercice 1 (factorisation QR)
La [factorisation QR](https://en.wikipedia.org/wiki/QR_decomposition) est un procédé permettant d'écrire une matrice réelle $A$ sous la forme d'un produit de la forme $A=QR$, dans lequel $Q$ est une matrice orthogonale et $R$ est une matrice triangulaire supérieure. Elle s'applique aussi bien à des matrice réelles carrées que rectangulaires.

On se propose dans cet exercice de mettre en &oelig;uvre la factorisation QR de deux manières distinctes pour des matrices réelles carrées inversibles.

Une première interprétation de la factorisation repose sur le [procédé d'orthonormalisation de Gram-Schmidt](https://en.wikipedia.org/wiki/Gram%E2%80%93Schmidt_process). Les colonnes de la matrice orthogonale $Q$ sont les vecteurs orthonormés obtenus à l'issue de l'application du procédé à la famille des colonnes de la matrice $A$, les coefficients des colonnes de la matrice triangulaire supérieure $R$ correspondant alors aux coefficients respectifs des colonnes de $A$ écrites dans la base orthonormées par les colonnes de $Q$ (ceux-ci sont des quantités calculées par l'algorithme du procédé de Gram-Schmidt).

**1.** En s'inspirant de l'algorithme du procédé d'orthonormalisation Gram-Schmidt modifié mis en &oelig;uvre dans une précédente feuille, écrire une fonction `QR_gramschmidt` retournant la factorisation QR d'une matrice carrée inversible obtenue par application du procédé de Gram-Schmidt.

**2.** Utiliser cette fonction pour résoudre le système linéaire $Ax=b$, avec
$$
A=\begin{pmatrix}3&17&10\\2&4&-2\\6&18&-12\end{pmatrix}\text{ et }b=\begin{pmatrix}1\\2\\3\end{pmatrix}.
$$
On pourra vérifier que le résultat trouvé est correct en le comparant à celui calculé par la commande `linalg.solve(A,b)` de NumPy.

In [ ]:
A=np.array([[3.,17.,10.],[2.,4.,-2.],[6.,18.,-12.]])
b=np.array([1.,2.,3.])

Même sous sa forme modifiée, le procédé d'orthonormalisation de Gram-Schmidt reste numériquement instable. Pour le calcul de la factorisation QR d'une matrice réelle, on lui préfère pour cette raison des méthodes reposant sur des isométries vectorielles, l'utilisation des [réflexions de Householder](https://en.wikipedia.org/wiki/Householder_transformation) étant l'une des approches possibles.

Étant donné un vecteur $\vec{v}$ de l'espace $\mathbb{R}^n$, la transformation de Householder associée au vecteur $\vec{v}$ est la symétrie orthogonale, ou réflexion, par rapport à l'hyperplan orthogonal à $\vec{v}$. Si la matrice colonne $v$ represente le vecteur $\vec{v}$ dans la base canonique de l'espace, la matrice $H_v$ de la transformation dans la base canonique est donnée par
$$
H_v=I_n-\frac{2}{v^\top v}vv^\top.
$$

**3.** Écrire une fonction `matrice_householder` ayant comme argument d'entrée un tableau contenant la matrice colonne $v$ représentant un vecteur $\vec{v}$ dans la base canonique et renvoyant la matrice $H_v$ de la transformation de Householder associée dans la base canonique.

La factorisation QR d'une matrice $A$ peut alors être obtenue de la manière suivante. On crée une suite de matrices $A^{(k)}$, $k=0,\dots,n-1$, en posant $A^{(0)}=A$ et en appliquant successivement des réflexions de Householder successives de manière à éliminer les coefficients situés sous la diagonale pour finalement obtenir la matrice $R=A^{(n-1)}$. Pour fabriquer la transformation de Householder annulant les coefficients sous-diagonaux de la $k+1$<sup>e</sup> colonne de la matrice courante $A^{(k)}$, $k=0,\dots,n-2$, on utilise le vecteur $\vec{v}^{(k+1)}$, dont les $k$ premières coordonnées sont nulles, dont la $k+1$<sup>e</sup> coordonnée vaut
$$
a^{(k)}_{k+1k+1}+\text{sign}(a^{(k)}_{k+1k+1})\|a^{(k)}_{k+1}\|_2
$$
où $\text{sign}(a^{(k)}_{k+1k+1})$ est le signe du coefficient $a^{(k)}_{k+1k+1}$ et $\|a^{(k)}_{k+1}\|_2$ est la norme euclidienne du vecteur de $\mathbb{R}^{n-k}$ ayant pour coordonnées $a^{(k)}_{i+k\,k+1}$, $i=1,\dots,n-k$, et dont les $n-k-1$ dernières valent respectivement $a^{(k)}_{ik}$, $i=k+2,\dots,n$.

La matrice $Q$ est alors obtenue en multipliant par la droite la matrice identité par les matrices (symétriques) des transformations de Householder successivement utilisées.

**4.** Écrire une fonction `QR_householder` retournant la factorisation QR d'une matrice carrée obtenue par applications successives de réflexions de Householder.

**5.** Utiliser cette nouvelle fonction pour résoudre le système linéaire précédent.

## Exercice bonus (factorisation QR par les rotations de Givens)
Une autre manière d'obtenir la factorisation QR d'une matrice carrée par le recours à des isométries vectorielles consiste à éliminer un à un les coefficients situés sous la diagonale en utilisant des rotations. Les matrices associées à ces transformations étant en effet orthogonales, le produit cumulé des transposées des matrices associées utilisées à chaque étape conduira bien à la matrice $Q$ de la factorisation à l'issue de l'élimination.

Pour mettre à zéro l'élément situé à la $i$<sup>e</sup> ligne et à la $j$<sup>e</sup> colonne, avec $j<i$, d'une matrice $A$ d'ordre $n$, on multiplie $A$ à gauche par la matrice de [rotation de Givens](https://en.wikipedia.org/wiki/Givens_rotation) donnée par
$$
G(i,j,\theta)=\begin{pmatrix}
1&0&\dots&\dots&\dots&\dots&\dots&\dots&\dots&\dots&0\\
0&1&&&&&&&&&\vdots\\
\vdots&&\ddots&&&&&&&&\vdots\\
\vdots&&&\cos(\theta)&&&&-\sin(\theta)&&&\vdots\\
\vdots&&&&1&&&&&&\vdots\\
\vdots&&&&&\ddots&&&&&\vdots\\
\vdots&&&&&&1&&&&\vdots\\
\vdots&&&\sin(\theta)&&&&\cos(\theta)&&&\vdots\\
\vdots&&&&&&&&1&&\vdots\\
\vdots&&&&&&&&&\ddots&0\\
0&\dots&\dots&\dots&\dots&\dots&\dots&\dots&\dots&0&1
\end{pmatrix}=I_n-(1-\cos(\theta))(E_{ii}+E_{jj})+\sin(\theta)(E_{ij}-E_{ji}),
$$
et représentant la rotation d'angle $\theta$ dans le plan engendré par les $i$<sup>e</sup> et $j$<sup>e</sup> vecteurs de la base canonique de $\mathbb{R}^n$. Pour déterminer la valeur de l'angle de rotation, on remarque que seules les $i$<sup>e</sup> et $j$<sup>e</sup> lignes de $A$ sont modifiées lors de la multiplication et l'on peut ainsi se ramener au problème suivant : trouver $\theta$ tel que
$$
\begin{pmatrix}\cos(\theta)&-\sin(\theta)\\\sin(\theta)&\cos(\theta)\end{pmatrix}\begin{pmatrix}a_{jj}\\a_{ij}\end{pmatrix}=\begin{pmatrix}\sqrt{{a_{jj}}^2+{a_{ij}}^2}\\0\end{pmatrix}.
$$
On peut également observer qu'il est seulement nécessaire de connaître les valeurs de $\cos(\theta)$ et $\sin(\theta)$ en pratique, pour lesquelles on a respectivement
$$
\cos(\theta)=\frac{a_{jj}}{\sqrt{{a_{jj}}^2+{a_{ij}}^2}}\text{ et }\sin(\theta)=-\frac{a_{ij}}{\sqrt{{a_{jj}}^2+{a_{ij}}^2}}.
$$

**1.** Écrire une fonction `matrice_Givens` ayant pour arguments d'entrée l'indice de ligne $i$ et l'indice de colonne $j$, les éléments $a_{jj}$ et $a_{ij}$, ainsi que l'ordre d'une matrice $A$ et renvoyant la matrice de Givens permettant d'éliminer l'élément $a_{ij}$ de $A$. Afin d'éviter les problèmes liés aux erreurs d'arrondi lors du calcul de $\sqrt{{a_{jj}}^2+{a_{ij}}^2}$, on fera appel à la fonction `hypot` de la bibliothèque `math` de Python.

In [ ]:
from math import hypot

**2.** Écrire une fonction `QR_Givens` retournant la factorisation QR d'une matrice carrée obtenue par applications successives de rotations de Givens.

**3.** Utiliser cette fonction pour résoudre le système linéaire considéré dans l'exercice précédent.